In [ ]:
# Import necessary libraries
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.feature_selection import SelectKBest, f_classif
from sklearn.preprocessing import StandardScaler
from keras.models import Sequential
from keras.layers import Dense, LSTM, GRU
from keras.wrappers.scikit_learn import KerasClassifier
from keras.optimizers import Adam, RMSprop, SGD
from keras.utils import np_utils

# Load your dataset
data = pd.read_csv('data.csv')

# Separate features and labels
X = data.drop('class', axis=1).values
y = data['class'].values

# Feature selection
selector = SelectKBest(score_func=f_classif, k=10)  # Adjust k value as needed
X_selected = selector.fit_transform(X, y)

# Split data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X_selected, y, test_size=0.2, random_state=42)

# Standardize features
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Convert labels to categorical
y_train = np_utils.to_categorical(y_train)
y_test = np_utils.to_categorical(y_test)

# Define a function to create LSTM model (for KerasClassifier)
def create_lstm_model(optimizer='adam', learn_rate=0.01):
    if optimizer == 'Adam':
        opt = Adam(learning_rate=learn_rate)
    elif optimizer == 'RMSprop':
        opt = RMSprop(learning_rate=learn_rate)
    elif optimizer == 'SGD':
        opt = SGD(learning_rate=learn_rate)
    
    model = Sequential()
    model.add(LSTM(100, input_shape=(X_train.shape[1],)))
    model.add(Dense(2, activation='softmax'))
    model.compile(loss='categorical_crossentropy', optimizer=opt, metrics=['accuracy'])
    return model

# Define a function to create GRU model (for KerasClassifier)
def create_gru_model(optimizer='adam', learn_rate=0.01):
    if optimizer == 'Adam':
        opt = Adam(learning_rate=learn_rate)
    elif optimizer == 'RMSprop':
        opt = RMSprop(learning_rate=learn_rate)
    elif optimizer == 'SGD':
        opt = SGD(learning_rate=learn_rate)
    
    model = Sequential()
    model.add(GRU(100, input_shape=(X_train.shape[1],)))
    model.add(Dense(2, activation='softmax'))
    model.compile(loss='categorical_crossentropy', optimizer=opt, metrics=['accuracy'])
    return model

# Wrap models in KerasClassifier for GridSearch
lstm_model = KerasClassifier(build_fn=create_lstm_model, verbose=0)
gru_model = KerasClassifier(build_fn=create_gru_model, verbose=0)

# Define the grid search parameters
batch_size = [16, 32, 64]
epochs = [50, 100, 300]
optimizer = ['Adam', 'RMSprop', 'SGD']
learn_rate = [0.01, 0.02, 0.03, 0.04]

param_grid = dict(batch_size=batch_size, epochs=epochs, optimizer=optimizer, learn_rate=learn_rate)

# For LSTM
grid_lstm = GridSearchCV(estimator=lstm_model, param_grid=param_grid, n_jobs=-1, cv=3)
grid_lstm_result = grid_lstm.fit(X_train, y_train)

# For GRU
grid_gru = GridSearchCV(estimator=gru_model, param_grid=param_grid, n_jobs=-1, cv=3)
grid_gru_result = grid_gru.fit(X_train, y_train)

# Print the best parameters for each model
print("Best LSTM: %f using %s" % (grid_lstm_result.best_score_, grid_lstm_result.best_params_))
print("Best GRU: %f using %s" % (grid_gru_result.best_score_, grid_gru_result.best_params_))

# Use the best parameters to retrain models
best_lstm = grid_lstm_result.best_estimator_.model
best_gru = grid_gru_result.best_estimator_.model

# Evaluate models with the test set
lstm_scores = best_lstm.evaluate(X_test, y_test, verbose=0)
gru_scores = best_gru.evaluate(X_test, y_test, verbose=0)

print("Best LSTM Accuracy: %.2f%%" % (lstm_scores[1]*100))
print("Best GRU Accuracy: %.2f%%" % (gru_scores[1]*100))

# Obtain predictions from the best models
lstm_predictions = best_lstm.predict(X_test)
gru_predictions = best_gru.predict(X_test)

# Convert predictions from one-hot encoding to class labels
lstm_class_predictions = np.argmax(lstm_predictions, axis=1)
gru_class_predictions = np.argmax(gru_predictions, axis=1)

# Majority voting
final_predictions = []
for lstm_pred, gru_pred in zip(lstm_class_predictions, gru_class_predictions):
    if lstm_pred == gru_pred:
        final_predictions.append(lstm_pred)
    else:
        final_predictions.append(np.random.choice([lstm_pred, gru_pred]))

# Convert final predictions to one-hot encoding for evaluation
final_predictions = np_utils.to_categorical(final_predictions)

# Evaluate the ensemble model
from sklearn.metrics import accuracy_score
ensemble_accuracy = accuracy_score(np.argmax(y_test, axis=1), np.argmax(final_predictions, axis=1))
print("Ensemble Accuracy: %.2f%%" % (ensemble_accuracy * 100))
